<a href="https://colab.research.google.com/github/ipeirotis-org/datasets/blob/main/Shapefiles/CensusShapefiles_to_Bigquery.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install -U -q pip tensorflow geopandas folium mapclassify google-cloud-storage google-cloud-bigquery[pandas] db-dtypes

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 21.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 475.2/475.2 MB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 48.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.3/100.3 kB 8.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.1/121.1 kB 11.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 222.8/222.8 kB 21.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 73.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 442.0/442.0 kB 42.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 51.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 183.3/183.3 kB 17.2 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
lida 0.0.10 r

In [43]:
import folium
import os
import requests
import zipfile
import geopandas as gpd
from tqdm import tqdm

import os
import zipfile
from google.cloud import storage, bigquery
import geopandas as gpd
import pandas as pd


The shapefiles are available at https://www2.census.gov/geo/tiger/TIGER2019/

In [44]:
# Path to your service account JSON file
service_account_json = 'nyu-datasets-77d8cc8e92d6.json'

# Set the environment variable
os.environ['GOOGLE_APPLICATION_CREDENTIALS'] = service_account_json

In [6]:
from google.colab import auth
auth.authenticate_user()

AuthorizationError: ignored

# US States and US Counties

In [69]:
state_url = 'https://www2.census.gov/geo/tiger/TIGER2019/STATE/tl_2019_us_state.zip'
states_gdf = gpd.GeoDataFrame.from_file(state_url)

In [70]:
counties_url = 'https://www2.census.gov/geo/tiger/TIGER2019/COUNTY/tl_2019_us_county.zip'
counties_gdf = gpd.GeoDataFrame.from_file(counties_url)

In [74]:
states = sorted(states_gdf['STATEFP'].values)

In [76]:
counties = counties_gdf.filter(['STATEFP', 'COUNTYFP']).values

In [87]:
counties = sorted(counties, key=lambda x: (x[0],x[1]))

# Download state, county, tract, water data to Google Bucket


In [9]:
def download_file_and_upload_to_gcs(url, local_path, bucket_name, destination_blob_name):
    """
    Downloads a file from a URL and uploads it to Google Cloud Storage.

    Args:
    url (str): URL of the file to download.
    local_path (str): Local path to save the file.
    bucket_name (str): Name of the GCS bucket.
    destination_blob_name (str): Destination blob name in the GCS bucket.
    """
    # Download file
    response = requests.get(url)
    with open(local_path, 'wb') as file:
        file.write(response.content)

    # Upload to Google Cloud Storage
    storage_client = storage.Client()
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(destination_blob_name)

    blob.upload_from_filename(local_path)

In [ ]:
# Download states
download_file_and_upload_to_gcs(state_url, 'maps/tl_2019_us_state.zip', 'census_shapefiles', 'states/tl_2019_us_state.zip')

In [ ]:
# Download counties
download_file_and_upload_to_gcs(counties_url, 'maps/tl_2019_us_county.zip', 'census_shapefiles', 'counties/tl_2019_us_county.zip')

In [ ]:
# Download tracts
for STATEFP in tqdm(states):
    filename = f"tl_2019_{STATEFP}_tract.zip"
    tract_url = f"https://www2.census.gov/geo/tiger/TIGER2019/TRACT/{filename}"
    download_file_and_upload_to_gcs(tract_url, f'maps/{filename}', 'census_shapefiles', f'tracts/{filename}')


In [ ]:
# Download blockgroups
for STATEFP in tqdm(states):
    filename = f"tl_2019_{STATEFP}_bg.zip"
    tract_url = f"https://www2.census.gov/geo/tiger/TIGER2019/BG/{filename}"
    download_file_and_upload_to_gcs(tract_url, f'maps/{filename}', 'census_shapefiles', f'blockgroups/{filename}')

In [ ]:
# Download blocks
for STATEFP in tqdm(states):
    filename = f"tl_2019_{STATEFP}_tabblock10.zip"
    tract_url = f"https://www2.census.gov/geo/tiger/TIGER2019/TABBLOCK/{filename}"
    download_file_and_upload_to_gcs(tract_url, f'maps/{filename}', 'census_shapefiles', f'blocks/{filename}')


In [ ]:
# Download water areas
for STATEFP, COUNTYFP in tqdm(counties):
    filename = f"tl_2019_{STATEFP+COUNTYFP}_areawater.zip"
    tract_url = f"https://www2.census.gov/geo/tiger/TIGER2019/AREAWATER/{filename}"
    download_file_and_upload_to_gcs(tract_url, f'maps/{filename}', 'census_shapefiles', f'areawater/{filename}')

# Merge Water Areas to State-based Files

In [67]:
def get_geodf_from_shp(bucket_name, shapefile_blob_name, temp_dir='temp'):
    # Initialize Google Cloud clients
    storage_client = storage.Client()

    # Create the temporary directory if it does not exist
    os.makedirs(temp_dir, exist_ok=True)

    # Download the shapefile ZIP from the bucket
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(shapefile_blob_name)

    # Create the full path for the zip file, ensuring all subdirectories exist
    zip_path = os.path.join(temp_dir, shapefile_blob_name)
    os.makedirs(os.path.dirname(zip_path), exist_ok=True)

    blob.download_to_filename(zip_path)

    # Extract the ZIP file
    with zipfile.ZipFile(zip_path, 'r') as zip_ref:
        zip_ref.extractall(temp_dir)

    # Find the .shp file inside the extracted folder
    shp_path = None
    for root, dirs, files in os.walk(temp_dir):
        for filename in files:
            if filename.endswith('.shp'):
                shp_path = os.path.join(root, filename)
                break
        if shp_path:
            break

    if not shp_path:
        raise FileNotFoundError("No .shp file found in the extracted ZIP.")

    # Read the shapefile into a GeoDataFrame
    gdf = gpd.read_file(shp_path)

    # Convert the geometries to a BigQuery-friendly format (e.g., WKT)
    gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)

    # Convert the GeoDataFrame to a Pandas DataFrame
    df = pd.DataFrame(gdf)

    # Clean up: remove temporary files and directories
    for root, dirs, files in os.walk(temp_dir, topdown=False):
        for name in files:
            os.remove(os.path.join(root, name))
        for name in dirs:
            os.rmdir(os.path.join(root, name))

    return df

def get_geodf_from_geojson(bucket_name, shapefile_blob_name, temp_dir='temp'):
    # Initialize Google Cloud clients
    storage_client = storage.Client()

    # Create the temporary directory if it does not exist
    os.makedirs(temp_dir, exist_ok=True)

    # Download the shapefile ZIP from the bucket
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(shapefile_blob_name)

    # Create the full path for the zip file, ensuring all subdirectories exist
    blob_path = os.path.join(temp_dir, shapefile_blob_name)
    os.makedirs(os.path.dirname(blob_path), exist_ok=True)

    blob.download_to_filename(blob_path)

    # Read the shapefile into a GeoDataFrame
    gdf = gpd.read_file(blob_path)

    # Convert the geometries to a BigQuery-friendly format (e.g., WKT)
    gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)

    # Convert the GeoDataFrame to a Pandas DataFrame
    df = pd.DataFrame(gdf)

    # Clean up: remove temporary files and directories
    for root, dirs, files in os.walk(temp_dir, topdown=False):
        for name in files:
            os.remove(os.path.join(root, name))
        for name in dirs:
            os.rmdir(os.path.join(root, name))

    return df


In [106]:
def save_geodfs_to_bucket(geodf_list, bucket_name, destination_blob_name, temp_file='temp.geojson'):
    """
    Combines a list of GeoDataFrames and saves them as one GeoDataFrame in a Google Cloud Storage bucket.

    Args:
    geodf_list (list): List of GeoDataFrames.
    bucket_name (str): Name of the Google Cloud Storage bucket.
    destination_blob_name (str): The destination file name in the bucket.
    temp_file (str, optional): Temporary local file name to store combined GeoDataFrame. Defaults to 'temp.geojson'.
    """

    combined_df = pd.concat(geodf_list, ignore_index=True)
    geom = gpd.GeoSeries.from_wkt(combined_df['geometry'])
    combined_df = combined_df.drop('geometry', axis='columns')

    # Combine GeoDataFrames
    combined_geodf = gpd.GeoDataFrame(combined_df, geometry=geom)
    combined_geodf.crs = {'init': 'epsg:4326'}

    # Save combined GeoDataFrame to a file
    combined_geodf.to_file(temp_file, driver='GeoJSON')

    # Initialize Google Cloud Storage client
    storage_client = storage.Client()

    # Upload the file to Google Cloud Storage
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(destination_blob_name)
    blob.upload_from_filename(temp_file)

    # Optionally, clean up the local temporary file
    os.remove(temp_file)

    print(f"Combined GeoDataFrame uploaded to {bucket_name}/{destination_blob_name}")


In [ ]:
# Merge water areas
for STATEFP in tqdm(states):
  state_gdfs = []
  for COUNTYFP in tqdm([c for s,c in counties if s==STATEFP]):
    # if s!=STATEFP: continue
    # print(f"{STATEFP}, {COUNTYFP}")
    filename = f"tl_2019_{STATEFP+COUNTYFP}_areawater.zip"
    gdf = get_geodf_from_shp('census_shapefiles', f'areawater/{filename}')
    gdf['STATEFP'] = STATEFP
    gdf['COUNTYFP'] = COUNTYFP
    state_gdfs.append(gdf)
  save_geodfs_to_bucket(state_gdfs, 'census_shapefiles', f"areawater_states/tl_2019_{STATEFP}_areawater.geojson")

  0%|          | 0/67 [00:00<?, ?it/s]<ipython-input-67-1d266f2795a8>:39: UserWarning: Geometry column does not contain geometry.
  gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)

  1%|▏         | 1/67 [00:02<02:23,  2.18s/it]<ipython-input-67-1d266f2795a8>:39: UserWarning: Geometry column does not contain geometry.
  gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)

  3%|▎         | 2/67 [00:05<03:16,  3.03s/it]<ipython-input-67-1d266f2795a8>:39: UserWarning: Geometry column does not contain geometry.
  gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)

  4%|▍         | 3/67 [00:06<02:08,  2.01s/it]<ipython-input-67-1d266f2795a8>:39: UserWarning: Geometry column does not contain geometry.
  gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)

  6%|▌         | 4/67 [00:08<02:00,  1.92s/it]<ipython-input-67-1d266f2795a8>:39: UserWarning: Geometry column does not contain geometry.
  gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)

  7%|▋         | 5

#  Import shapes to Bigquery

In [12]:
def upload_geodf_to_bigquery(df, bigquery_dataset_id, bigquery_table_id):

    bigquery_client = bigquery.Client()

    # Create a BigQuery table and upload the DataFrame
    table_id = f"{bigquery_dataset_id}.{bigquery_table_id}"
    job = bigquery_client.load_table_from_dataframe(df, table_id)
    job.result()  # Wait for the job to complete

    sql = f"""
        CREATE OR REPLACE TABLE `{bigquery_dataset_id}.{bigquery_table_id}` AS
          SELECT *, ST_GeogFromText(geometry) AS geography
          FROM `{bigquery_dataset_id}.{bigquery_table_id}`;
        ALTER TABLE `{bigquery_dataset_id}.{bigquery_table_id}`
        DROP COLUMN geometry;
    """
    query_job = bigquery_client.query(sql)
    query_job.result()  # Wait for the query to complete


In [ ]:
gdf = get_geodf_from_shp('census_shapefiles', 'states/tl_2019_us_state.zip')
upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_states')

In [ ]:
gdf = get_geodf_from_shp('census_shapefiles', 'counties/tl_2019_us_county.zip')
upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_counties')

In [ ]:
for STATEFP in tqdm(states):
    filename = f"tracts/tl_2019_{STATEFP}_tract.zip"
    gdf = get_geodf_from_shp('census_shapefiles', filename)
    upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_tracts')

In [ ]:
for STATEFP in tqdm(states):
    filename = f"blockgroups/tl_2019_{STATEFP}_bg.zip"
    gdf = get_geodf_from_shp('census_shapefiles', filename)
    upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_blockgroups')

In [ ]:
for STATEFP in tqdm(states):
    filename = f"blocks/tl_2019_{STATEFP}_tabblock10.zip"
    gdf = get_geodf_from_shp('census_shapefiles', filename)
    upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_blocks')

In [ ]:
for STATEFP in tqdm(states):
  filename = f'areawater_states/tl_2019_{STATEFP}_areawater.geojson'
  gdf = get_geodf_from_geojson('census_shapefiles', filename)
  upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'areawater')

# Subtract Area Water

In [32]:
pre_aggregate_query = """
CREATE OR REPLACE TABLE `shapefiles.us_counties_nowater` AS

WITH WaterAgg AS (
  SELECT
    A.STATEFP,
    A.COUNTYFP,
    ST_Union_Agg(A.geography) AS agg_geography
  FROM
    `nyu-datasets.shapefiles.areawater` AS A
  GROUP BY
    A.STATEFP, A.COUNTYFP
)
SELECT
  C.GEOID, C.STATEFP, C.COUNTYFP,
  ST_Difference(C.geography, WA.agg_geography) AS diff_geography
FROM
  `nyu-datasets.shapefiles.us_counties` AS C
LEFT JOIN
  WaterAgg AS WA
ON
  C.STATEFP = WA.STATEFP AND C.COUNTYFP = WA.COUNTYFP

"""

bigquery_client = bigquery.Client()
bigquery_client.query(pre_aggregate_query).result()


In [57]:
bigquery_client = bigquery.Client()

sql = """
  SELECT
    A.STATEFP,
    A.COUNTYFP,
    ST_Union_Agg(A.geography) AS agg_geography
  FROM
    `nyu-datasets.shapefiles.areawater` AS A
  WHERE A.STATEFP='31' AND A.COUNTYFP='061'
  GROUP BY
    A.STATEFP, A.COUNTYFP
"""

df = bigquery_client.query(sql)

In [58]:
gdf = df.to_geodataframe()

In [92]:
STATEFP = '01'
filename = f'areawater_states/tl_2019_{STATEFP}_areawater.geojson'
gdf = get_geodf_from_geojson('census_shapefiles', filename)


<ipython-input-67-1d266f2795a8>:74: UserWarning: Geometry column does not contain geometry.
  gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)


In [100]:
gdf2 = gdf.query("COUNTYFP == '003'")
geom = gpd.GeoSeries.from_wkt(gdf2['geometry'])
gdf2 = gdf2.drop('geometry', axis='columns')
gdf2 = gpd.GeoDataFrame(gdf2, geometry=geom)
gdf2

ANSICODE        HYDROID     FULLNAME  MTFCC  ALAND   AWATER     INTPTLAT  \
620      None   110167718368  Bay Minette  H2051      0  1989280  +30.6974568   
621      None   110167720492         None  H2030      0    33363  +30.8696858   
622      None   110167720223         None  H2030      0     2245  +30.7332110   
623      None   110167720701         None  H2030      0    18670  +30.8308266   
624      None   110167720643         None  H2030      0    11902  +30.6972652   
...       ...            ...          ...    ...    ...      ...          ...   
2932     None   110167719060         None  H2030      0      692  +30.3860392   
2933     None   110167719076         None  H2030      0     2569  +30.3880940   
2934     None   110167719453         None  H2030      0     5808  +30.4436935   
2935     None   110167719471         None  H2030      0      339  +30.3302828   
2936     None  1103690633679         None  H2030      0     1475  +30.2635751   

         INTPTLON STATEFP COUNTYFP  \
620   -87.9161990      01      003   
621   -87.6395283      01      003   
622   -87.8748014      01      003   
623   -87.8677462      01      003   
624   -87.7708086      01      003   
...           ...     ...      ...   
2932  -87.7186743      01      003   
2933  -87.7101170      01      003   
2934  -87.7304091      01      003   
2935  -87.6650384      01      003   
2936  -87.6138960      01      003   

                                               geometry  
620   POLYGON ((-87.92505 30.69587, -87.92477 30.696...  
621   POLYGON ((-87.64108 30.86999, -87.64104 30.870...  
622   POLYGON ((-87.87501 30.73350, -87.87500 30.733...  
623   POLYGON ((-87.86867 30.83099, -87.86840 30.831...  
624   POLYGON ((-87.77146 30.69725, -87.77136 30.697...  
...                                                 ...  
2932  POLYGON ((-87.71882 30.38604, -87.71878 30.386...  
2933  POLYGON ((-87.71047 30.38824, -87.71039 30.388...  
2934  POLYGON ((-87.73107 30.44559, -87.73105 30.445...  
2935  POLYGON ((-87.66514 30.33036, -87.66491 30.330...  
2936  POLYGON ((-87.61451 30.26332, -87.61428 30.263...  

[2317 rows x 11 columns]

/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)


In [105]:
gdf2.query("COUNTYFP == '003'").explore(
    figsize=(20, 20),
    edgecolor="black",
    linewidth=0.5,
    zorder=0,
)